In [23]:
import os
pdbid_general = [item for item in os.listdir("v2020-other-PL") if item not in ["readme", "index"]]
pdbid_refined = [item for item in os.listdir("refined-set") if item not in ["readme", "index"]]
pdbids = pdbid_general + pdbid_refined
# pdbids = [item for item in os.listdir("v2020-other-PL") if item not in ["readme", "index"]]

In [46]:
pdbid_core = [item for item in os.listdir("CASF-2016/coreset/")]

In [24]:
len(pdbids)

19443

In [9]:
!mkdir tmp

In [4]:
import multiprocessing
from multiprocessing.pool import ThreadPool

def download_pdb(pdbid):
    os.system("wget -O tmp/{}.pdb https://files.rcsb.org/header/{}.pdb > /dev/null".format(pdbid, pdbid))

In [5]:
pool=ThreadPool(16)
pool.map(download_pdb, pdbids)

--2023-02-01 15:53:33--  https://files.rcsb.org/header/4ps0.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/5t1s.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/4r1y.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/5ovh.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/5e1e.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/1kwr.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/2g5p.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/1q3d.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/5am4.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/2qhc.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/4k8o.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/2n7b.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/2wpb.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/3vqs.pdb
--2023-02-01 15:53:33--  https://files.rcsb.org/header/4fhi.pdb
Resolving files.rcsb.org (files.rcsb.org

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [8]:
from Bio.PDB.parse_pdb_header import parse_pdb_header
from tqdm import tqdm

headers = {}
for pdbid in tqdm(pdbids):
    # os.system("wget -O tmp/{}.pdb https://files.rcsb.org/download/{}.pdb".format(pdbid, pdbid))
    header = parse_pdb_header(f"tmp/{pdbid}.pdb")
    headers[pdbid] = header["head"]

100%|██████████| 19443/19443 [02:27<00:00, 131.68it/s]


In [69]:
import datetime
datetime.datetime.strptime(
    header["deposition_date"], '%Y-%m-%d')

datetime.datetime(2008, 8, 22, 0, 0)

In [70]:
resolutions={}
dates={}
for pdbid in tqdm(pdbids):
    header=parse_pdb_header(f"tmp/{pdbid}.pdb")
    resolutions[pdbid]=header["resolution"]
    dates[pdbid]=datetime.datetime.strptime(
        header["release_date"], '%Y-%m-%d')


100%|██████████| 19443/19443 [01:19<00:00, 245.97it/s]


In [9]:
import pandas as pd

sr=pd.Series(headers)

In [11]:
sr.to_csv("pdb_headers.csv")

In [18]:
sr.value_counts()[:20]

hydrolase                            3326
transferase                          3035
hydrolase/hydrolase inhibitor        2046
transferase/transferase inhibitor    1851
transcription                         672
lyase                                 635
immune system                         459
signaling protein                     443
transport protein                     436
oxidoreductase                        412
ligase                                270
membrane protein                      229
isomerase                             218
chaperone                             217
sugar binding protein                 214
protein binding                       205
lyase/lyase inhibitor                 193
viral protein                         167
cell cycle                            150
ligase/ligase inhibitor               148
dtype: int64

In [21]:
from rdkit import Chem
mol=Chem.SDMolSupplier("v2020-other-PL/1a1b/1a1b_ligand.sdf")[0]

In [22]:
Chem.MolToSmiles(Chem.RemoveHs(mol))

'CCCCCN(CCCCC)C(=O)C(CCC(=O)O)NC(=O)C(Cc1ccc(OP(=O)(O)O)cc1)NC(C)=O'

In [19]:
df=pd.DataFrame(sr, columns=["header"])

In [20]:
df

header
6r8o                      isomerase
3fh7  hydrolase/hydrolase inhibitor
4b7r                      hydrolase
3qfd                  immune system
3fvn               membrane protein
...                             ...
6npt                    transferase
3pax                    transferase
5ezz            hydrolase/inhibitor
1hgi                  viral protein
3e9i                         ligase

[19443 rows x 1 columns]

In [39]:
smiles={}
for pdbid in tqdm(pdbid_general):
    try:
        mol2=Chem.MolFromMol2File(f"v2020-other-PL/{pdbid}/{pdbid}_ligand.mol2")
        mol2_noH=Chem.RemoveHs(mol2)
        smi=Chem.MolToSmiles(mol2_noH)
    except:
        try:
            sdf=Chem.SDMolSupplier(f"v2020-other-PL/{pdbid}/{pdbid}_ligand.sdf")
            sdf_noH=Chem.RemoveHs(sdf[0])
            smi=Chem.MolToSmiles(sdf_noH)
        except:
            smi=""
    smiles[pdbid]=smi

for pdbid in tqdm(pdbid_refined):
    try:
        mol2=Chem.MolFromMol2File(f"refined-set/{pdbid}/{pdbid}_ligand.mol2")
        mol2_noH=Chem.RemoveHs(mol2)
        smi=Chem.MolToSmiles(mol2_noH)
    except:
        try:
            sdf=Chem.SDMolSupplier(f"refined-set/{pdbid}/{pdbid}_ligand.sdf")
            sdf_noH=Chem.RemoveHs(sdf[0])
            smi=Chem.MolToSmiles(sdf_noH)
        except:
            smi=""
    smiles[pdbid]=smi

  0%|          | 7/14127 [00:00<35:44,  6.58it/s][17:31:50] 2lct_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
[17:31:50] 6ax4_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
  0%|          | 17/14127 [00:00<25:47,  9.12it/s][17:31:50] 2pjb_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
[17:31:50] 4gdy_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
  0%|          | 27/14127 [00:00<18:47, 12.51it/s][17:31:50] 1g9s_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
[17:31:50] 1q6m_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
  0%|          | 37/14127 [00:00<13:51, 16.95it/s][17:31:50] 3m89_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
[17:31:50] Can't kekulize mol.  Unkekulized atoms: 22 23 24 27 31

[17:31:50] ERROR: Could not sanitize molecule ending on line 101
[17:31:50] ERROR: Can't kekulize mol.  Unkekulized atoms: 22 23 24 27 31

[17:31:50] 2xlc_ligand: warning - O.co2 with non C.2 or S.o2 neighbor.
[17:31:50] non-ring atom 6 

In [40]:
sr_smi=pd.Series(smiles)

In [42]:
sr_smi.value_counts()

                                                                                                                                                                                        322
Nc1ncnc2c1ncn2C1OC(COP(=O)(O)OP(=O)(O)O)C(O)C1O                                                                                                                                          81
Nc1ncnc2c1ncn2C1OC(COP(=O)(O)OP(=O)(O)OP(=O)(O)O)C(O)C1O                                                                                                                                 75
CC(C)CN(C[C@@H](O)[C@H](Cc1ccccc1)NC(=O)O[C@H]1CO[C@H]2OCC[C@@H]12)S(=O)(=O)c1ccc(N)cc1                                                                                                  38
Nc1ncnc2c1ncn2[C@@H]1O[C@H](CSCC[C@H]([NH3+])C(=O)[O-])[C@@H](O)[C@H]1O                                                                                                                  38
                                                            

In [44]:
df["smiles"]=sr_smi

In [48]:
df["category"]=sr_category

In [47]:
sr_category={}
for pdbid in pdbid_general:
    sr_category[pdbid]="general"
for pdbid in pdbid_refined:
    sr_category[pdbid]="refined"
for pdbid in pdbid_core:
    sr_category[pdbid]="core"

sr_category=pd.Series(sr_category)

In [74]:
df.to_csv("info.csv")

In [50]:
df[df.category=="core"]

header  \
3b65                          transcription   
1lpg                              hydrolase   
1g2k                              hydrolase   
3tsk          hydrolase/hydrolase inhibitor   
3u8k  acetylcholine-binding protein/agonist   
...                                     ...   
4m0z      transferase/transferase inhibitor   
4eky                            transferase   
3g2n                            transferase   
4dli      transferase/transferase inhibitor   
1o5b              blood clotting, hydrolase   

                                                 smiles category  
3b65    C[C@](O)(COc1ccc(C#N)cc1)C(=O)Nc1ccc(C#N)c(I)c1     core  
1lpg  C[N+](C)(C)c1ccc(CNC(=O)c2cc3cc(OCc4ccccc4)ccc...     core  
1g2k  CNC(=O)c1cccc(CN2[C@H](COc3ccccc3)[C@H](O)[C@@...     core  
3tsk  NC(=O)CC[C@H](NC(=O)CCc1ccc(-c2cc(-c3ccccc3)cs...     core  
3u8k                        CCOc1cncc(N2CCC[NH2+]CC2)c1     core  
...                                                 ...      ...  
4m0z        COc1ccc2cccc(-n3cc(NC(N)=O)c(C(N)=O)n3)c2c1     core  
4eky  CCCC#Cc1cn([C@@H]2O[C@H](CO)[C@@H](O)[C@H](O)[...     core  
3g2n  O=C(N[C@@H]1O[C@H](CO)[C@@H](O)[C@H](O)[C@H]1O...     core  
4dli                 Nc1ccc2c(NC3CC3)nc(-c3ccccc3)nc2c1     core  
1o5b                        NC(=[NH2+])c1cc2c(I)cccc2s1     core  

[285 rows x 3 columns]

In [5]:
from Bio import PDB
parser = PDB.PDBParser()
header = parser.get_header("https://files.rcsb.org/view/6upj.pdb")

TypeError: get_header() takes 1 positional argument but 2 were given

In [38]:

Chem.MolToSmiles(Chem.RemoveHs(Chem.MolFromMol2File("v2020-other-PL/3rzi/3rzi_ligand.mol2")))

'[NH3+][C@@H](Cc1c[nH]c2ccccc12)C(=O)[O-]'

In [8]:
parse_pdb_header("6upj.pdb")

{'name': 'hiv-2 protease/u99294 complex',
 'head': 'hydrolase',
 'idcode': '6UPJ',
 'deposition_date': '1996-12-10',
 'release_date': '1997-04-21',
 'structure_method': 'x-ray diffraction',
 'resolution': 2.34,
 'structure_reference': ['h.i.skulnick,p.d.johnson,w.j.howe,p.k.tomich,k.-t.chok.d.watenpaugh,m.n.janakiraman,l.a.dolak,j.p.mcgrath,j.c.lynn,m.-m.horng,r.r.hinshaw,g.l.zipp,m.j.ruwart, f.j.schwende,w.-z.zhong,g.e.padbury,r.j.dalga,l.shioup.l.possert,b.d.rush,k.f.wilkinson,g.m.howard,l.n.totm.g.williams,t.j.kakuk,s.l.cole,r.m.zaya,k.d.lovasz, j.k.morris,k.r.romines,s.thaisrivongs,p.a.aristoff structure-based design of sulfonamide-substituted non-peptidic hiv protease inhibitors. j.med.chem. v. 38 4968 1995 issn 0022-2623 8544171 '],
 'journal_reference': 'k.r.romines,k.d.watenpaugh,p.k.tomich,w.j.howe,j.k.mok.d.lovasz,a.m.mulichak,b.c.finzel,j.c.lynn,m.-m.hornf.j.schwende,m.j.ruwart,g.l.zipp,k.-t.chong,l.a.dolakl.n.toth,g.m.howard,b.d.rush,k.f.wilkinson,p.l.posserr.j.dalga,r.r.hi

In [57]:
from get_header_seq import get_seq_
def get_seq_str(addr):
    seqs=list(get_seq_(addr).values())
    seq_dedup = list(set(seqs))
    if len(seq_dedup)==1:
        return seq_dedup[0]
    else:
        return ":".join(seqs)


In [56]:
list(set(list(get_seq_("refined-set/1a4r/1a4r_protein.pdb").values())))

['MQTIKCVVVGDVAVGKTCLLISYTTNKFPSEYVPTVFDNYAVTVMIGGEPYTLGLFDTAGQEDYDRLRPLSYPQTDVFLVCFSVVSPSSFENVKEKWVPEITHHCPKTPFLLVGTQIDLRDDPSTIEKLAKNKQKPITPETAEKLARDLKAVKYVECSALTQKGLKNVFDEAILAALEPPEPKKSRRCVL']

In [58]:
seqs={}
for pdbid in tqdm(pdbid_general):
    try:
        seq=get_seq_str(f"v2020-other-PL/{pdbid}/{pdbid}_protein.pdb")
    except:
        seq=""
    seqs[pdbid]=seq

for pdbid in tqdm(pdbid_refined):
    try:
        seq=get_seq_str(f"refined-set/{pdbid}/{pdbid}_protein.pdb")
    except:
        seq=""
    seqs[pdbid]=seq

sr_seq=pd.Series(seqs)

100%|██████████| 5316/5316 [01:12<00:00, 73.40it/s]


In [60]:
df["seq"]=sr_seq 

In [71]:
sr_resolution=pd.Series(resolutions)
sr_date=pd.Series(dates)

In [72]:
df["resolution"]=sr_resolution
df["date"]=sr_date

In [73]:
df

header  \
6r8o                      isomerase   
3fh7  hydrolase/hydrolase inhibitor   
4b7r                      hydrolase   
3qfd                  immune system   
3fvn               membrane protein   
...                             ...   
6npt                    transferase   
3pax                    transferase   
5ezz            hydrolase/inhibitor   
1hgi                  viral protein   
3e9i                         ligase   

                                                 smiles category  \
6r8o  CSc1ccccc1[C@H]1CCCN1C(=O)CNC(=O)NCc1ccc2c(c1)...  refined   
3fh7  O=C([O-])CCC[N@H+]1CCC[C@H]1COc1ccc(Oc2ccc(Cl)...  refined   
4b7r  CCC(CC)O[C@@H]1C[C@H](C(=O)[O-])C[C@H]([NH3+])...  refined   
3qfd  CC[C@H](C)[C@H](NC(=O)CNC(=O)[C@H](C)NC(=O)[C@...  refined   
3fvn  [NH3+][C@@H](C[C@]1(C(=O)[O-])C[C@H]2OCC[C@@H]...  refined   
...                                                 ...      ...   
6npt  CC(C)(C)c1ccc(C(=O)Nc2cc(-c3ccccc3)nn2-c2ccccc...  general   
3pax                                 COc1cccc(C(N)=O)c1  general   
5ezz  Cc1cc([C@@]2(c3cccc(-c4cncc(Cl)c4)c3)COC(=[NH2...  general   
1hgi  CO[C@]1(C(=O)[O-])C[C@H](OC(C)=O)[C@@H](NC(C)=...  general   
3e9i  Nc1ncnc2c1ncn2C1OC(COP(=O)(O)ONC(=O)C([NH3+])C...  general   

                                                    Seq  resolution       date  
6r8o  GNPLVYLDVDANGKPLGRVVLELKADVVPKTAENFRALCTGEKGFG...        1.36 2019-11-27  
3fh7  VDTCSLASPASVCRTKHLHLRCSVDFTRRTLTGTAALTVQSQEDNL...        2.05 2010-01-05  
4b7r  VKLAGNSSLCPVSGWAIYSKDNSVRIGSKGDVFVIREPFISCSPLE...        1.90 2012-10-03  
3qfd  GSHSMRYFFTSVSRPGRGEPRFIAVGYVDDTQFVRFDSDAASQRME...        1.68 2011-09-28  
3fvn  ANRTLIVTTILEEPYVMYRKSDKPLYGNDRFEGYCLDLLKELSNIL...        1.50 2010-01-19  
...                                                 ...         ...        ...  
6npt  IENCVHHIKRRDIVLKWELGEGAFGKVFLAECHNLLPEQDKMLVAV...        2.19 2019-05-22  
3pax  KSKLAKPIQDLIKMIFDVESMKKAMVEFEIDLQKMPLGKLSKRQIQ...        2.40 1998-05-27  
5ezz  RGSFVEMVDNLRGKSGQGYYVEMTVGSPPQTLNILVDTGSSNFAVG...        2.10 2016-02-24  
1hgi  QDLPGNDNSTATLCLGHHAVPNGTLVKTITDDQIEVTNATELVQSS...        2.70 1994-01-31  
3e9i  ELNDQLRVRREKLKKIEELGVDPFGKRFERTHKAEELFELYGDLSK...        2.20 2009-07-14  

[19443 rows x 6 columns]